In [0]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from pandas import Series,DataFrame
from datetime import date
import datetime as DT
import io
from scipy import stats
from sklearn.metrics import accuracy_score


In [0]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import xgboost
import csv as csv
from xgboost import plot_importance
from matplotlib import pyplot
from sklearn.model_selection import cross_val_score,KFold

from sklearn.metrics import mean_absolute_error
import matplotlib.pyplot as plt
from sklearn.model_selection import GridSearchCV   #Perforing grid search
from scipy.stats import skew
from collections import OrderedDict


In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
train=pd.read_csv("/content/drive/My Drive/dsn test 2 updated/train_car0408.csv", low_memory=False)
test=pd.read_csv("/content/drive/My Drive/dsn test 2 updated/test_car0408.csv", low_memory=False)
sample_format=pd.read_csv("/content/drive/My Drive/dsn test 2 updated/sample_car0408.csv", low_memory=False)

In [4]:
#Creating and storing our target variable in a seperate dataframe
carprice=DataFrame(train["naira_price"])

#This one is for our naira_price in the carprice dataframe
na_values=['07/03/2016 00:00','nan', '13/03/2016 00:00','20/03/2016 00:00', '24/03/2016 00:00','27/03/2016 00:00','25/03/2016 00:00', '26/03/2016 00:00','NaN']

carprice.naira_price=carprice['naira_price'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

carprice.naira_price = carprice.naira_price.fillna(288000)


#Here we want to merge our training and test set but for the columns to be same, we must first take of our target in train
train=train.drop(['naira_price'], axis=1)

#Now we merge BUT first we must create 2 train columns in our test and train set in order to id and seperate them later
train['train']=1
test['train']=0

#we join the test and train sets together for uniform cleaning
combined=pd.concat([train, test])


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:19: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



In [5]:
carprice.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224537 entries, 0 to 224536
Data columns (total 1 columns):
naira_price    224537 non-null object
dtypes: object(1)
memory usage: 1.7+ MB


In [6]:
carprice.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224537 entries, 0 to 224536
Data columns (total 1 columns):
naira_price    224537 non-null object
dtypes: object(1)
memory usage: 1.7+ MB


WE START WITH     **1. CAR BRAND**

In [7]:
"""na_values : scalar, str, list-like, or dict, optional

    Additional strings to recognize as NA/NaN. If dict passed, specific per-column NA values. By default the following values are interpreted as NaN: ‘’, ‘#N/A’, ‘#N/A N/A’, ‘#NA’, ‘-1.#IND’, ‘-1.#QNAN’, ‘-NaN’, ‘-nan’, ‘1.#IND’, ‘1.#QNAN’, ‘N/A’, ‘NA’, ‘NULL’, ‘NaN’, ‘n/a’, ‘nan’, ‘null’."""



'na_values : scalar, str, list-like, or dict, optional\n\n    Additional strings to recognize as NA/NaN. If dict passed, specific per-column NA values. By default the following values are interpreted as NaN: ‘’, ‘#N/A’, ‘#N/A N/A’, ‘#NA’, ‘-1.#IND’, ‘-1.#QNAN’, ‘-NaN’, ‘-nan’, ‘1.#IND’, ‘1.#QNAN’, ‘N/A’, ‘NA’, ‘NULL’, ‘NaN’, ‘n/a’, ‘nan’, ‘null’.'

In [8]:
combined.car_brand.unique()

array(['audi', 'volkswagen', 'skoda', 'bmw', 'mazda', 'nissan', 'renault',
       'ford', 'opel', 'mercedes_benz', 'honda', 'fiat', 'mini', 'smart',
       'hyundai', 'seat', 'subaru', 'volvo', 'mitsubishi', 'kia',
       'peugeot', 'suzuki', 'vauxhall', 'porsche', 'citroen', 'chevrolet',
       'sonstige_autos', 'dacia', 'daihatsu', 'alfa_romeo', 'toyota',
       'chrysler', 'daewoo', 'rover', 'jeep', 'saab', 'innoson',
       'land_rover', 'trabant', 'lotus', '0', '150000', '5000', '40000',
       '50000', '09/03/2016', 'manuell', nan, '90000'], dtype=object)

In [0]:
na_values= [ '0', '150000', '5000', '40000',
            '50000', '09/03/2016', 'manuell','90000']

combined.car_brand=combined['car_brand'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.car_brand = combined.car_brand.fillna('volkswagen')


In [10]:
combined.car_brand.value_counts()

volkswagen        71644
bmw               38033
mercedes_benz     34062
opel              33752
audi              31074
ford              21480
renault           15029
peugeot            9978
fiat               8133
seat               6272
skoda              5453
smart              5110
mazda              5075
citroen            4674
toyota             4548
nissan             4433
hyundai            3453
mini               3336
sonstige_autos     3068
volvo              3028
mitsubishi         2598
honda              2566
kia                2411
porsche            2106
suzuki             2097
alfa_romeo         2086
chevrolet          1770
chrysler           1294
dacia               887
jeep                773
land_rover          757
subaru              657
daihatsu            613
innoson             598
saab                490
daewoo              417
vauxhall            395
trabant             390
rover               378
lotus               205
Name: car_brand, dtype: int64

**CAR TYPE**

In [11]:
combined.car_type.unique()


array(['coupé', 'small car', 'limousine', 'station wagon', nan, 'bus',
       'other', 'convertible', '125000', 'test', 'control', '102',
       'privat'], dtype=object)

In [12]:
combined.car_type.value_counts()

limousine        89874
small car        68464
station wagon    63124
bus              29255
convertible      22201
coupé            17632
other             2828
test                 7
control              3
privat               2
102                  1
125000               1
Name: car_type, dtype: int64

In [0]:
na_values=['125000', 'test', 'control', '102',
       'privat']

combined.car_type=combined['car_type'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.car_type = combined.car_type.fillna('limousine')


**COUNTRY OF USE**

In [14]:
combined.country_of_use.unique()


array(['london', '2002', 'Land_Rover_Defender_110_Tdi',
       'Mercedes_A_160_Automatik', 'Auto_Mit_Tuev_und_Anhaengerkupplung',
       'Mercedes_Benz_280SL_Pagode',
       'Renault_Clio_1.6_Automatik_RXE_Tuev_Neu',
       'Ford_Fiesta_1.25_SYNC_Edition_82PS__Unfallfrei_mit_Garantie',
       'Mercedes_Benz_CLA_200_Urban',
       'Skoda_Octavia_Combi_1.6_Ambiente""/Autogas_Diamantsilber_Metallic"',
       'Golf_3_GT_Special_mit_Tuning',
       'Prius__Hybrid__+_1A_TOP_+_VOLLAUSSTATTUNG_+_IPA!',
       'Renault_Grand_Scenic_1.9_dCi_TÜV_NEU.KLIMA._7Sitzer'],
      dtype=object)

In [0]:
na_values=['2002', 'Land_Rover_Defender_110_Tdi',
       'Mercedes_A_160_Automatik', 'Auto_Mit_Tuev_und_Anhaengerkupplung',
       'Mercedes_Benz_280SL_Pagode',
       'Renault_Clio_1.6_Automatik_RXE_Tuev_Neu',
       'Ford_Fiesta_1.25_SYNC_Edition_82PS__Unfallfrei_mit_Garantie',
       'Mercedes_Benz_CLA_200_Urban',
       'Skoda_Octavia_Combi_1.6_Ambiente""/Autogas_Diamantsilber_Metallic"',
       'Golf_3_GT_Special_mit_Tuning',
       'Prius__Hybrid__+_1A_TOP_+_VOLLAUSSTATTUNG_+_IPA!',
       'Renault_Grand_Scenic_1.9_dCi_TÜV_NEU.KLIMA._7Sitzer']

combined.country_of_use=combined['country_of_use'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.country_of_use = combined.country_of_use.fillna('london')


In [16]:
combined.date_of_advert.unique()


array(['24/03/2016', '17/03/2016', '31/03/2016', '04/04/2016',
       '26/03/2016', '07/04/2016', '21/03/2016', '20/03/2016',
       '23/03/2016', '27/03/2016', '13/03/2016', '18/03/2016',
       '07/03/2016', '08/03/2016', '29/03/2016', '25/03/2016',
       '28/03/2016', '01/04/2016', '30/03/2016', '15/03/2016',
       '22/03/2016', '10/03/2016', '09/02/2016', '05/03/2016',
       '11/03/2016', '09/03/2016', '12/03/2016', '02/04/2016',
       '16/03/2016', '14/03/2016', '03/04/2016', '05/04/2016',
       '19/03/2016', '12/02/2016', '06/03/2016', '01/03/2016',
       '04/03/2016', '06/04/2016', '15/02/2016', '03/03/2016',
       '14/01/2016', '24/02/2016', '27/02/2016', '20/03/2015',
       '28/02/2016', '20/02/2016', '29/02/2016', '10/02/2016',
       '21/02/2016', '19/01/2016', '19/02/2016', '11/02/2016',
       '10/01/2016', '06/02/2016', '18/02/2016', '26/02/2016',
       '02/02/2016', '02/03/2016', '28/01/2016', '16/02/2016',
       '13/02/2016', '22/02/2016', '23/02/2016', '17/11

In [0]:
na_values=['land_rover', 'mercedes_benz', 'renault',
       'ford', 'octavia','150000', 'volkswagen', 'toyota']

combined.date_of_advert=combined['date_of_advert'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.date_of_advert = combined.date_of_advert.fillna('28/03/2016')


In [18]:
combined.date_of_advert.value_counts()

03/04/2016    13196
04/04/2016    12715
20/03/2016    12188
12/03/2016    12183
21/03/2016    11914
28/03/2016    11816
02/04/2016    11795
14/03/2016    11774
07/03/2016    11548
19/03/2016    11489
09/03/2016    11423
01/04/2016    11418
29/03/2016    11381
08/03/2016    11166
30/03/2016    11143
15/03/2016    11087
25/03/2016    11014
11/03/2016    11001
10/03/2016    10903
26/03/2016    10842
22/03/2016    10726
23/03/2016    10717
31/03/2016    10676
17/03/2016    10366
16/03/2016    10165
27/03/2016    10135
24/03/2016     9985
05/03/2016     7695
13/03/2016     5775
06/03/2016     5211
              ...  
22/01/2016        2
16/01/2016        2
23/11/2015        2
26/01/2016        2
04/09/2015        2
18/01/2016        2
09/09/2015        1
14/10/2015        1
28/12/2015        1
08/01/2016        1
10/03/2014        1
13/11/2015        1
17/12/2015        1
06/12/2015        1
14/01/2016        1
07/08/2015        1
10/11/2015        1
02/11/2015        1
11/06/2015        1


**GAS TYPE**

In [19]:
combined.gas_type.unique()


array(['diesel', 'gasoline', nan, 'liquefied petroleum gas', 'other',
       'compressed natural gas', '19/03/2016 00:00', 'defender',
       'a_klasse', 'c_klasse', 'andere', 'clio', 'fiesta', 'manuell',
       '2002', '2000', 'golf'], dtype=object)

In [0]:
na_values= ['19/03/2016 00:00', 'defender','a_klasse', 'c_klasse', 'andere', 'clio', 'fiesta', 'manuell', '2002', '2000', 'golf']

combined.gas_type=combined['gas_type'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.gas_type = combined.gas_type.fillna('gasoline')


In [21]:
combined.gas_type.unique()

array(['diesel', 'gasoline', 'liquefied petroleum gas', 'other',
       'compressed natural gas'], dtype=object)

**GEAR TYPE**

In [22]:
combined.gear_type.unique()


array(['manuell', 'automatik', nan, '19/03/2016 17:43', 'diesel',
       'benzin', '1440000', 'lupo', 'vectra', 'hybrid'], dtype=object)

In [0]:
na_values= ['19/03/2016 17:43', 'diesel',
       'benzin', '1440000', 'lupo', 'vectra', 'hybrid']
combined.gear_type=combined['gear_type'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.gear_type = combined.gear_type.fillna('manuell')


In [24]:
combined.gear_type.value_counts()


manuell      260949
automatik     74174
Name: gear_type, dtype: int64

**HORSE POWER**

In [25]:
combined.horse_power.unique()

array(['190', '75', '69', '102', '101', '105', '140', '136', '231', '90',
       '118', '193', '99', '60', '218', '122', '0', '129', '306', '95',
       '61', '177', '109', '170', '55', '143', '64', '160', '150', '50',
       '156', '80', '82', '204', '185', '87', '113', '86', '131', '163',
       '224', '200', '178', '265', '77', '110', '54', '286', '116', '184',
       '126', '194', '115', '305', '197', '120', '179', '235', '88',
       '313', '41', '45', '125', '165', '98', '130', '56', '326', '201',
       '213', '107', '83', '174', '100', '220', '73', '68', '66', '299',
       '74', '52', '510', '147', '310', '97', '65', '295', '203', '5',
       '144', '58', '300', '85', '245', '258', '84', '292', '239', '320',
       '63', '81', '148', '70', '145', '180', '260', '457', '104', '409',
       '250', '188', '114', '117', '192', '155', '39', '272', '92', '51',
       '135', '59', '230', '435', '209', '67', '344', '72', '249', '103',
       '279', '23', '138', '256', '175', '96', '226

In [0]:
na_values= ['renault', 'manuell', 'automatik', 'skoda','test']
combined.horse_power=combined['horse_power'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.horse_power = combined.horse_power.fillna(101)


**LAST ADVERT ONLINE**

In [27]:
combined.last_advert_online.unique()

array(['07/04/2016', '17/03/2016', '06/04/2016', '31/03/2016',
       '05/04/2016', '13/03/2016', '18/03/2016', '26/03/2016',
       '09/03/2016', '29/03/2016', '30/03/2016', '03/04/2016',
       '21/03/2016', '19/03/2016', '16/03/2016', '04/04/2016',
       '01/04/2016', '22/03/2016', '25/03/2016', '11/03/2016',
       '15/03/2016', '12/03/2016', '23/03/2016', '20/03/2016',
       '28/03/2016', '14/03/2016', '27/03/2016', '10/03/2016',
       '02/04/2016', '07/03/2016', '06/03/2016', '08/03/2016',
       '24/03/2016', '05/03/2016', nan, 'ja', 'nein', '8', '4'],
      dtype=object)

In [0]:
na_values= ['ja', 'nein', '8', '4']
combined.last_advert_online=combined['last_advert_online'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.last_advert_online = combined.last_advert_online.fillna('06/04/2016')


**MILEAGE**

In [29]:
combined.mileage.unique()

array([201125.0, 241350.0, 144810.0, 112630.0, 96540.0, 32180.0, 160900.0,
       128720.0, 8045.0, 80450.0, 64360.0, 16090.0, 48270.0, nan, 113.0,
       100.0, 0.0, 170.0, 90.0, 82.0, 156.0, '201125', '241350', '48270',
       '160900', '8045', '112630', '80450', '96540', '16090', '144810',
       '128720', '32180', '64360', 'kleinwagen', '90', '77', '131'],
      dtype=object)

In [0]:
na_values= [156.0, 82.0, 100.0, 90.0, 113.0,'90',170.0,'131','77', 'kleinwagen', 0.0 ]

combined.mileage=combined['mileage'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.mileage = combined.mileage.fillna(241350.0)


In [31]:
combined.mileage.value_counts()

241350.0    143013
241350       70237
201125.0     23613
201125       12053
160900.0      9937
144810.0      8026
128720.0      7155
112630.0      6376
96540.0       5638
80450.0       5061
160900        4881
64360.0       4187
144810        3963
48270.0       3936
32180.0       3532
128720        3497
112630        3106
8045.0        2900
96540         2833
80450         2360
64360         2057
48270         1844
32180         1752
8045          1440
16090.0       1168
16090          558
Name: mileage, dtype: int64

**MODEL**

In [32]:
combined.model.unique()

array([nan, 'golf', 'fabia', '3er', '3_reihe', 'passat', 'navara',
       'twingo', 'c_max', '5er', 'meriva', 'andere', 'civic', 'punto',
       'clio', 'e_klasse', 'kangoo', 'one', 'fortwo', '1er', 'b_klasse',
       'signum', 'astra', 'jetta', 'scirocco', 'polo', 'fiesta',
       'c_klasse', 'micra', 'vito', 'sprinter', 'escort', 'forester',
       'xc_reihe', 'scenic', 'a1', 'insignia', 'a_klasse', 'a4', 'tt',
       'a6', 'jazz', 'transporter', '7er', '80', 'glk', 'z_reihe',
       'sportage', 'sorento', 'ibiza', 'mustang', 'getz', 'ka', 'megane',
       'lupo', 'a3', 'zafira', '2_reihe', 'corsa', 'cordoba', 'vectra',
       'berlingo', 'm_klasse', 'touran', 'tiguan', 'i_reihe', 'sharan',
       '6_reihe', 'c4', 'panda', '5_reihe', 'yeti', 'octavia', 'mii',
       'mondeo', '6er', 'modus', 'fox', 'matiz', 'beetle', 'c1', 'rio',
       'logan', 'caddy', 'omega', 'cuore', 's_max', 'a2', 'x_reihe', 'a5',
       '147', 'galaxy', 'c3', 's_klasse', 'eos', 'avensis', 'viano', 'sl',
      

In [0]:
na_values= ['0','80','500','159','911','900','850','9000','200','156','90','100','145' ]

combined.model=combined['model'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.model = combined.model.fillna('a4')


In [34]:
combined.model.value_counts()

a4                    29613
golf                  27033
andere                23918
3er                   19250
polo                  10644
corsa                  9848
passat                 9618
astra                  9422
c_klasse               8505
5er                    8235
e_klasse               7318
a3                     6408
a6                     5790
focus                  5514
transporter            5309
fiesta                 4648
2_reihe                4595
fortwo                 4254
a_klasse               4129
twingo                 3829
1er                    3793
vectra                 3489
touran                 3488
3_reihe                3127
clio                   3053
mondeo                 2982
zafira                 2969
punto                  2683
megane                 2501
ibiza                  2407
                      ...  
r19                      81
crossfire                66
range_rover_evoque       65
gl                       63
lanos               

In [35]:
combined.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 335123 entries, 0 to 110585
Data columns (total 20 columns):
ID                      335123 non-null int64
Unnamed: 18             0 non-null float64
car_brand               335123 non-null object
car_name                335123 non-null object
car_type                335123 non-null object
country_of_use          335123 non-null object
date_of_advert          335123 non-null object
gas_type                335123 non-null object
gear_type               335123 non-null object
horse_power             335123 non-null object
last_advert_online      335123 non-null object
mileage                 335123 non-null object
model                   335123 non-null object
postal_code             335123 non-null object
registration_month      335123 non-null object
repair_status           279793 non-null object
scrapped_date           335123 non-null object
seller_type             335123 non-null object
train                   335123 non-null int64
ye

**POSTAL CODE**

1.  suspected for angebot



In [36]:
combined.postal_code.unique()

array(['66954', '91074', '60437', ..., '78586', '78598', '86944'],
      dtype=object)

In [37]:
combined.postal_code.value_counts()

10115    816
65428    586
66333    293
38518    292
44145    286
52525    282
32257    279
78224    278
60311    275
13357    270
51065    267
53757    266
40764    263
50354    262
26789    262
48599    261
48249    258
61169    257
65719    250
60386    249
85055    239
63263    238
13409    238
52249    236
92637    236
30419    236
52428    235
56070    232
65549    232
45326    232
        ... 
87674      1
86747      1
54484      1
91744      1
91369      1
78598      1
82067      1
29496      1
37297      1
25889      1
38879      1
14828      1
91743      1
21274      1
88719      1
55499      1
95358      1
1998       1
91289      1
21712      1
31094      1
21710      1
29473      1
24864      1
97780      1
82447      1
78345      1
31097      1
38877      1
97773      1
Name: postal_code, Length: 8138, dtype: int64

In [0]:
#for registration_month
na_values=['Angebot', 'nan','NaN', ]

combined.postal_code=combined['postal_code'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.postal_code = combined.postal_code.fillna(10115)


In [0]:
combined.postal_code=pd.to_numeric(combined.postal_code, errors='coerce')

In [40]:
#REGISTRATION MONTH
combined.registration_month.unique()

array(['5', '6', '7', '10', '0', '12', '3', '2', '9', '11', '1', '4', '8',
       'benzin', '1997', '2000', '1994', '1970', '1999', '2014', '2013',
       'gasoline', 8, 11, 2, 1, 4, 0, 7, 3, 9, 12, 10, 5, 6, 2690, 1993,
       2006], dtype=object)

In [41]:
combined.registration_month.value_counts()

3           22533
6           20681
4           19031
5           19016
7           18172
10          17159
0           16744
11          16071
12          15919
9           15712
1           14977
8           14674
2           13839
3           11062
6           10107
4            9531
5            9318
7            8817
10           8484
0            8249
11           7876
9            7795
12           7667
8            7463
1            7456
2            6757
2006            2
2000            1
2013            1
1999            1
benzin          1
2690            1
1997            1
gasoline        1
1970            1
2014            1
1993            1
1994            1
Name: registration_month, dtype: int64

In [0]:
#for registration_month
na_values=['benzin', '1997', '2000', '1994', '1970', '1999', '2014', '2013',
       'gasoline', 2690, 1993, 2006]

combined.registration_month=combined['registration_month'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.registration_month = combined.registration_month.fillna(3)


In [43]:
combined.repair_status.unique()

array(['Yes', 'No', nan, '51645', '10', '4', '6', '7', '15/03/2016',
       'nein', 'ja', '75', '0'], dtype=object)

In [0]:
#for registration_month
na_values=['51645', '10', '4', '6', '7', '15/03/2016',
       'nein', 'ja', '75', '0']

combined.repair_status=combined['repair_status'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.repair_status = combined.repair_status.fillna('Yes')


In [45]:
#SCRAPPED DATE
combined.scrapped_date.unique()

array(['24/03/2016', '17/03/2016', '31/03/2016', '04/04/2016',
       '26/03/2016', '07/04/2016', '21/03/2016', '20/03/2016',
       '23/03/2016', '27/03/2016', '13/03/2016', '18/03/2016',
       '07/03/2016', '08/03/2016', '29/03/2016', '25/03/2016',
       '28/03/2016', '01/04/2016', '30/03/2016', '15/03/2016',
       '22/03/2016', '10/03/2016', '05/03/2016', '11/03/2016',
       '09/03/2016', '12/03/2016', '02/04/2016', '16/03/2016',
       '14/03/2016', '03/04/2016', '05/04/2016', '19/03/2016',
       '06/03/2016', '06/04/2016', 'NaT'], dtype=object)

In [0]:
na_values=['NaT']

combined.scrapped_date=combined['scrapped_date'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.scrapped_date = combined.scrapped_date.fillna('03/04/2016')


In [47]:
combined.scrapped_date.value_counts()

03/04/2016    13136
04/04/2016    12685
12/03/2016    12247
20/03/2016    12159
14/03/2016    12148
07/03/2016    11943
21/03/2016    11874
02/04/2016    11841
19/03/2016    11824
28/03/2016    11783
01/04/2016    11472
09/03/2016    11408
29/03/2016    11367
08/03/2016    11199
30/03/2016    11186
15/03/2016    11117
25/03/2016    10991
11/03/2016    10984
10/03/2016    10954
22/03/2016    10830
26/03/2016    10804
23/03/2016    10725
31/03/2016    10650
17/03/2016    10497
27/03/2016    10206
16/03/2016    10090
24/03/2016     9982
05/03/2016     8611
13/03/2016     5330
06/03/2016     4865
18/03/2016     4365
05/04/2016     4266
06/04/2016     1052
07/04/2016      532
Name: scrapped_date, dtype: int64

In [48]:
#SELLER_TYPE
combined.seller_type.unique()

array(['private', 'kleinwagen', '07/03/2016 10:57', '13/03/2016 15:52',
       '20/03/2016 15:30', '24/03/2016 16:52', '27/03/2016 16:52',
       '25/03/2016 19:52', '26/03/2016 18:25', '09/03/2016 17:37',
       '25/03/2016 11:45', '03/04/2016 22:52', '16/03/2016 20:52'],
      dtype=object)

In [0]:
na_values=['kleinwagen', '07/03/2016 10:57', '13/03/2016 15:52',
       '20/03/2016 15:30', '24/03/2016 16:52', '27/03/2016 16:52',
       '25/03/2016 19:52', '26/03/2016 18:25', '09/03/2016 17:37',
       '25/03/2016 11:45', '03/04/2016 22:52', '16/03/2016 20:52']

combined.seller_type=combined['seller_type'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.seller_type = combined.seller_type.fillna('private')


In [50]:
combined.year_of_registration.unique()

array(['2013', '2003', '2010', '1997', '2000', '2006', '2007', '2009',
       '2004', '2018', '1992', '2005', '2001', '2014', '2008', '2002',
       '1995', '1999', '2015', '2012', '1996', '2011', '1993', '1998',
       '2016', '1970', '1984', '2017', '1994', '1978', '1985', '1961',
       '1983', '1973', '1989', '1975', '1987', '1990', '1969', '1982',
       '1986', '1972', '1988', '1991', '1967', '1947', '1976', '1981',
       '1957', '1980', '1979', '1965', '1968', '1971', '1974', '1977',
       '1966', '1960', '1963', '1958', '1964', '1962', '1953', '1959',
       '1951', '1956', '1954', '1955', '1952', '4', 'suv', 'kleinwagen',
       'limousine', 'cabrio', 'coupe', '241350', '1949', '1950', '1948',
       'Angebot', 'andere', 'bus'], dtype=object)

In [0]:
na_values=['4', 'suv', 'kleinwagen','limousine', 'cabrio', 'coupe', '241350',
       'Angebot', 'andere', 'bus']

combined.year_of_registration=combined['year_of_registration'].replace(to_replace=na_values, value=np.nan, inplace=False, limit=None, regex=False, method='pad')

combined.year_of_registration = combined.year_of_registration.fillna('2006')


In [52]:
combined.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 335123 entries, 0 to 110585
Data columns (total 20 columns):
ID                      335123 non-null int64
Unnamed: 18             0 non-null float64
car_brand               335123 non-null object
car_name                335123 non-null object
car_type                335123 non-null object
country_of_use          335123 non-null object
date_of_advert          335123 non-null object
gas_type                335123 non-null object
gear_type               335123 non-null object
horse_power             335123 non-null object
last_advert_online      335123 non-null object
mileage                 335123 non-null object
model                   335123 non-null object
postal_code             335123 non-null int64
registration_month      335123 non-null object
repair_status           335123 non-null object
scrapped_date           335123 non-null object
seller_type             335123 non-null object
train                   335123 non-null int64
yea

In [53]:
#converting columns to strings
combined.car_brand.to_string()
combined.car_name.to_string()
combined.car_type.to_string()
combined.country_of_use.to_string()
combined.date_of_advert.to_string()
combined.gas_type.to_string()
combined.gear_type.to_string()

combined.last_advert_online.to_string()

combined.model.to_string()

combined.registration_month.to_string()
combined.repair_status.to_string()
combined.scrapped_date.to_string()
combined.seller_type.to_string()
combined.year_of_registration.to_string()

'0         2013\n1         2003\n2         2010\n3         1997\n4         2000\n5         2006\n6         2007\n7         2013\n8         2006\n9         2009\n10        2004\n11        2018\n12        1992\n13        2004\n14        2010\n15        2005\n16        2018\n17        2009\n18        2006\n19        2018\n20        2004\n21        2004\n22        2009\n23        2010\n24        2001\n25        2009\n26        2014\n27        2010\n28        2018\n29        2010\n30        2007\n31        2001\n32        2008\n33        2018\n34        2000\n35        2008\n36        2009\n37        2018\n38        2010\n39        2002\n40        2003\n41        1995\n42        1999\n43        2004\n44        2010\n45        2008\n46        2015\n47        2005\n48        2002\n49        2008\n50        2012\n51        1996\n52        2007\n53        1999\n54        2007\n55        2003\n56        2011\n57        2006\n58        2015\n59        2011\n60        2005\n61        2015\n62     

In [0]:
#converting columns to numeric
combined.horse_power=pd.to_numeric(combined.horse_power, errors='coerce')

combined.postal_code=pd.to_numeric(combined.postal_code, errors='coerce')

combined.mileage=pd.to_numeric(combined.mileage, errors='coerce')

carprice.naira_price=pd.to_numeric(carprice.naira_price, errors='coerce')

In [55]:
combined.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 335123 entries, 0 to 110585
Data columns (total 20 columns):
ID                      335123 non-null int64
Unnamed: 18             0 non-null float64
car_brand               335123 non-null object
car_name                335123 non-null object
car_type                335123 non-null object
country_of_use          335123 non-null object
date_of_advert          335123 non-null object
gas_type                335123 non-null object
gear_type               335123 non-null object
horse_power             335123 non-null int64
last_advert_online      335123 non-null object
mileage                 335123 non-null float64
model                   335123 non-null object
postal_code             335123 non-null int64
registration_month      335123 non-null object
repair_status           335123 non-null object
scrapped_date           335123 non-null object
seller_type             335123 non-null object
train                   335123 non-null int64
yea

In [56]:
carprice.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224537 entries, 0 to 224536
Data columns (total 1 columns):
naira_price    224537 non-null int64
dtypes: int64(1)
memory usage: 1.7 MB


In [0]:
#processing another time column
#Here we format the time/date column to a pandas datetime format where we can extract other useable features
combined['date_of_advert']=pd.to_datetime(combined.date_of_advert, errors='coerce')

combined['DayOfWeekt']=combined.date_of_advert.dt.weekday_name

#indicating the day of the year in numbers....non categorical
combined['DayOfYeart']=combined.date_of_advert.dt.dayofyear

#this is indicating the day of the month in numbers...this wont be treated as a categorical var
combined['DayOfmontht']=combined.date_of_advert.dt.day

#this is indicating the number of days in the month of that transaction...this wont be treated as a categorical var
combined['DaysInMontht']=combined.date_of_advert.dt.daysinmonth

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthEndOrNott']=combined.date_of_advert.dt.is_month_end

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthStartOrNott']=combined.date_of_advert.dt.is_month_start

#this is indicating if its beginning of quarter or not in boolean...this wont be treated as a categorical var
combined['IsQuarterStartt']=combined.date_of_advert.dt.is_quarter_start

#this is indicating if its end of month or not in boolean...this wont be treated as a categorical var
combined['IsQuarterEndt']=combined.date_of_advert.dt.is_quarter_end

In [0]:
#Here we format the time/date column to a pandas datetime format where we can extract other useable features
combined['last_advert_online']=pd.to_datetime(combined.last_advert_online, errors='coerce')

combined['DayOfWeektr']=combined.last_advert_online.dt.weekday_name

#indicating the day of the year in numbers....non categorical
combined['DayOfYeartr']=combined.last_advert_online.dt.dayofyear

#this is indicating the day of the month in numbers...this wont be treated as a categorical var
combined['DayOfmonthtr']=combined.last_advert_online.dt.day

#this is indicating the number of days in the month of that transaction...this wont be treated as a categorical var
combined['DaysInMonthtr']=combined.last_advert_online.dt.daysinmonth

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthEndOrNottr']=combined.last_advert_online.dt.is_month_end

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthStartOrNottr']=combined.last_advert_online.dt.is_month_start

#this is indicating if its beginning of quarter or not in boolean...this wont be treated as a categorical var
combined['IsQuarterStarttr']=combined.last_advert_online.dt.is_quarter_start

#this is indicating if its end of month or not in boolean...this wont be treated as a categorical var
combined['IsQuarterEndtr']=combined.last_advert_online.dt.is_quarter_end

In [0]:
#Now we would be converting datetime atributes
#Here we format the time/date column to a pandas datetime format where we can extract other useable features
combined['scrapped_date']=pd.to_datetime(combined.scrapped_date, errors='coerce')
combined['DayOfWeek']=combined.scrapped_date.dt.weekday_name

#indicating the day of the year in numbers....non categorical
combined['DayOfYear']=combined.scrapped_date.dt.dayofyear

#this is indicating the day of the month in numbers...this wont be treated as a categorical var
combined['DayOfmonth']=combined.scrapped_date.dt.day

#this is indicating the number of days in the month of that transaction...this wont be treated as a categorical var
combined['DaysInMonth']=combined.scrapped_date.dt.daysinmonth

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthEndOrNot']=combined.scrapped_date.dt.is_month_end

#this is indicating if its end of month or not in boolean...this would be treated as a categorical var
combined['MonthStartOrNot']=combined.scrapped_date.dt.is_month_start

#this is indicating if its beginning of quarter or not in boolean...this wont be treated as a categorical var
combined['IsQuarterStart']=combined.scrapped_date.dt.is_quarter_start

#this is indicating if its end of month or not in boolean...this wont be treated as a categorical var
combined['IsQuarterEnd']=combined.scrapped_date.dt.is_quarter_end




In [0]:
#we are dropping car name because of its weight and inability for kaggle or google's kernel to process it
combined=combined.drop(['car_name'], axis=1)
combined=combined.drop(['ID'], axis=1)
combined=combined.drop(['Unnamed: 18'], axis=1)
combined=combined.drop(['seller_type'], axis=1)
combined=combined.drop(['country_of_use'], axis=1)


In [0]:

#now we encode



In [0]:
#NOW WE ENCODE

combined3=pd.get_dummies(combined['car_type'], drop_first=True)


combined4=pd.get_dummies(combined['year_of_registration'], drop_first=True)
#now we encode
combined5=pd.get_dummies(combined['registration_month'], drop_first=True)
#now we encode
combined6=pd.get_dummies(combined['gas_type'], drop_first=True)

combined7=pd.get_dummies(combined['car_brand'], drop_first=True)
#now we encode
combined8=pd.get_dummies(combined['repair_status'], drop_first=True)
#now we encode
combined9=pd.get_dummies(combined['gear_type'], drop_first=True)

combined10=pd.get_dummies(combined['model'], drop_first=True)


combined11=pd.get_dummies(combined['MonthEndOrNot'],drop_first=True)
#now we encode
combined12=pd.get_dummies(combined['DayOfWeek'], drop_first=True)
#now we encode
combined13=pd.get_dummies(combined['MonthStartOrNot'], drop_first=True)
#now we encode
combined14=pd.get_dummies(combined['IsQuarterStart'], drop_first=True)
#now we encode
combined15=pd.get_dummies(combined['IsQuarterEnd'], drop_first=True)


combined16=pd.get_dummies(combined['MonthEndOrNott'],drop_first=True)
#now we encode
combined17=pd.get_dummies(combined['DayOfWeekt'], drop_first=True)
#now we encode
combined18=pd.get_dummies(combined['MonthStartOrNott'], drop_first=True)
#now we encode
combined19=pd.get_dummies(combined['IsQuarterStartt'], drop_first=True)
#now we encode
combined20=pd.get_dummies(combined['IsQuarterEndt'], drop_first=True)


combined21=pd.get_dummies(combined['MonthEndOrNottr'],drop_first=True)
#now we encode
combined22=pd.get_dummies(combined['DayOfWeektr'], drop_first=True)
#now we encode
combined23=pd.get_dummies(combined['MonthStartOrNottr'], drop_first=True)
#now we encode
combined24=pd.get_dummies(combined['IsQuarterStarttr'], drop_first=True)
#now we encode
combined25=pd.get_dummies(combined['IsQuarterEndtr'], drop_first=True)

In [0]:
#we are dropping encoded columns 
combined=combined.drop(['year_of_registration'], axis=1)
combined=combined.drop(['registration_month'], axis=1)
combined=combined.drop(['gas_type'], axis=1)
combined=combined.drop(['car_brand'], axis=1)
combined=combined.drop(['repair_status'], axis=1)
combined=combined.drop(['gear_type'], axis=1)
combined=combined.drop(['model'], axis=1)
combined=combined.drop(['car_type'], axis=1)

#Now we drop the weblog_date column since we have processed it
combined=combined.drop(['scrapped_date'], axis=1)
combined=combined.drop(['date_of_advert'], axis=1)
combined=combined.drop(['last_advert_online'], axis=1)

combined=combined.drop(['MonthEndOrNot'],axis=1)
#now we encode
combined=combined.drop(['DayOfWeek'], axis=1)
#now we encode
combined=combined.drop(['MonthStartOrNot'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterStart'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterEnd'], axis=1)


combined=combined.drop(['MonthEndOrNott'],axis=1)
#now we encode
combined=combined.drop(['DayOfWeekt'], axis=1)
#now we encode
combined=combined.drop(['MonthStartOrNott'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterStartt'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterEndt'], axis=1)



combined=combined.drop(['MonthEndOrNottr'],axis=1)
#now we encode
combined=combined.drop(['DayOfWeektr'], axis=1)
#now we encode
combined=combined.drop(['MonthStartOrNottr'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterStarttr'], axis=1)
#now we encode
combined=combined.drop(['IsQuarterEndtr'], axis=1)



In [63]:
combined.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 335123 entries, 0 to 110585
Data columns (total 13 columns):
horse_power      335123 non-null int64
mileage          335123 non-null float64
postal_code      335123 non-null int64
train            335123 non-null int64
DayOfYeart       335123 non-null int64
DayOfmontht      335123 non-null int64
DaysInMontht     335123 non-null int64
DayOfYeartr      335123 non-null int64
DayOfmonthtr     335123 non-null int64
DaysInMonthtr    335123 non-null int64
DayOfYear        335123 non-null int64
DayOfmonth       335123 non-null int64
DaysInMonth      335123 non-null int64
dtypes: float64(1), int64(12)
memory usage: 35.8 MB


In [0]:
#combined=combined.drop(['postal_code'], axis=1)

In [0]:
#now we combine all datasets together
combined=pd.concat([combined,combined3,combined4,combined5,combined6,combined7,combined8,combined9,combined10], axis=1)


In [154]:
combined.postal_code.mean()

51268.099503764286

In [155]:
combined.mileage.mean()

201505.23279512298

In [156]:
combined.horse_power.mean()

120.69325590902444

In [0]:
#feature engineering
combined['willa']=combined.postal_code-combined.horse_power

combined['olla']= combined.postal_code+combined.horse_power

combined['fella']=combined.postal_code/combined.horse_power

combined['tola']=combined.mileage/combined.horse_power

combined['bola']=combined.mileage-combined.horse_power

combined['vola']=combined.mileage+combined.horse_power

combined['lola']=combined.mileage+combined.postal_code

combined['bula']=combined.mileage-combined.postal_code

combined['mola']=combined.mileage/combined.postal_code







In [176]:
#Now its time to separate those two datasets and we are done with both the train and test set now 
#containing the same number of columns.
train_df=combined[combined['train']==1]
test_df=combined[combined['train']==0]
#we now drop the train columns we created in test and train set
train_df.drop(['train'], axis=1, inplace=True)
test_df.drop(['train'], axis=1, inplace=True)


/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [0]:
#now we combine back our target to our train set together
train_df=pd.concat([train_df,carprice], axis=1)

In [178]:
train_df.shape

(224537, 409)

In [161]:
test_df.shape

(110586, 408)

In [0]:
train_df['target']=train_df.naira_price>2262534.141277384

In [0]:
# Encoding the INDEPENDENT Variable
from sklearn.preprocessing import LabelEncoder
labelencoder_X = LabelEncoder()
train_df['target'] = labelencoder_X.fit_transform(train_df.target)

In [111]:
train_df.head()

horse_power   mileage  postal_code  ...  zafira  naira_price  target
0          190  201125.0        66954  ...       0      6588000       1
1           75  241350.0        91074  ...       0       540000       0
2           69  144810.0        60437  ...       0      1296000       0
3          102  241350.0        33775  ...       0       234000       0
4          101  241350.0        27472  ...       0       359640       0

[5 rows x 401 columns]

In [107]:
train_df.naira_price.mean()

2262534.141277384

In [181]:
train_df.shape

(224537, 410)

In [0]:
#Splitting  the dataset into X and y
#X = train_df.iloc[:, 0:408].values
#y = train_df.iloc[:, -1].values

#Splitting  the dataset into X and y
X = train_df.iloc[:, 0:409].values
y = train_df.iloc[:, -1].values



In [186]:
# Splitting the dataset into the Training set and validation set
#from sklearn.model_selection import train_test_split
#X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state =0)


#"""#Here we are generating our synthetic points to balance the scarce class using the SMOTE method
from imblearn.over_sampling import SMOTE
sm=SMOTE(random_state=12, ratio=1.0)
X_train_new, y_train_new = sm.fit_sample(X, y)

ValueError: ignored

In [0]:
X_train_x=X_train_new[:, 0:409]
y_train_y=X_train_new[:, -1]

In [128]:
y_train_y[0:5]

array([ 648000., 5396400.,  306000.,  352800., 3780000.])

In [126]:
X_train_x.shape

(229278, 399)

In [0]:
# Feature Scaling
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

In [169]:
# Fitting Simple Linear Regression to the Training set
from sklearn.linear_model import LinearRegression
regressor = LinearRegression()
regressor.fit(X_train, y_train)
#regressor.fit(X_train_x, y_train_y)

# Predicting the Test set results
y_pred = regressor.predict(X_test)
regressor.score(X_test, y_test)


ValueError: ignored

In [164]:
# Fitting Decision Tree Regression to the dataset
from sklearn.tree import DecisionTreeRegressor
regressor = DecisionTreeRegressor(random_state = 0)
regressor.fit(X_train, y_train)

# Predicting a new result
y_pred = regressor.predict(X_test)
regressor.score(X_test, y_test)


#regressor.fit(X, y)


1.0

In [165]:
# Fitting Random Forest Regression to the dataset
from sklearn.ensemble import RandomForestRegressor
regressor = RandomForestRegressor(n_estimators = 10, random_state = 0)
regressor.fit(X_train_x, y_train_y)

#Predicting a new result
y_pred = regressor.predict(X_test)
regressor.score(X_test, y_test)

#regressor.fit(X, y)

# Calculate the Root Mean Squared Error
print("RMSE: %.2f"
      % math.sqrt(np.mean((regr.predict(X_test) - y_test) ** 2)))

KeyboardInterrupt: ignored

In [0]:
# Let's try XGboost algorithm to see if we can get better results
xgb = xgboost.XGBRegressor(n_estimators=50, learning_rate=0.08, gamma=0, subsample=0.75,
                           colsample_bytree=1, max_depth=5)


In [152]:
xgb.fit(X_train_x, y_train_y)

/usr/local/lib/python3.6/dist-packages/xgboost/core.py:614: UserWarning: Use subset (sliced data) of np.ndarray is not recommended because it will generate extra copies and increase memory consumption
  "because it will generate extra copies and increase memory consumption")


[14:40:37] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=1, gamma=0,
             importance_type='gain', learning_rate=0.08, max_delta_step=0,
             max_depth=5, min_child_weight=1, missing=None, n_estimators=50,
             n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
             reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
             silent=None, subsample=0.75, verbosity=1)

In [136]:
pip install catboost


     |████████████████████████████████| 61.8MB 63.8MB/s 


In [170]:
import catboost
from catboost import CatBoostRegressor

cbc = CatBoostRegressor()
cbc.fit(X_train_x, y_)

0:	learn: 3751855.0268962	total: 106ms	remaining: 1m 46s
1:	learn: 3675243.5454243	total: 194ms	remaining: 1m 36s
2:	learn: 3602430.6970320	total: 281ms	remaining: 1m 33s
3:	learn: 3532695.0409920	total: 380ms	remaining: 1m 34s
4:	learn: 3465902.7859169	total: 469ms	remaining: 1m 33s
5:	learn: 3401509.1477127	total: 559ms	remaining: 1m 32s
6:	learn: 3339654.1104257	total: 653ms	remaining: 1m 32s
7:	learn: 3278722.5518235	total: 734ms	remaining: 1m 30s
8:	learn: 3220807.8175427	total: 821ms	remaining: 1m 30s
9:	learn: 3164888.8831103	total: 907ms	remaining: 1m 29s
10:	learn: 3111703.2811192	total: 1s	remaining: 1m 30s
11:	learn: 3060927.9698972	total: 1.09s	remaining: 1m 29s
12:	learn: 3011338.8268731	total: 1.18s	remaining: 1m 29s
13:	learn: 2963542.0864825	total: 1.27s	remaining: 1m 29s
14:	learn: 2917121.4564546	total: 1.37s	remaining: 1m 29s
15:	learn: 2872664.0353958	total: 1.46s	remaining: 1m 30s
16:	learn: 2830408.8518430	total: 1.55s	remaining: 1m 29s
17:	learn: 2790436.2957053	

In [0]:
# Predicting the Test set results and converting to csv
dftest_pred= cbc.predict(test_df.values)
prediction = pd.DataFrame(dftest_pred, columns=['naira_price']).to_csv('prediction_auto6.csv')